# **LongMemory.jl**: Generating, Estimating, and Forecasting Long Memory

Models in ***Julia***

Illustrative example

[J. Eduardo Vera-Valdés](https://everval.github.io)
[](https://orcid.org/0000-0002-0337-8055)
(Aalborg University)

**LongMemory.jl** is a package for time series long memory modelling in
***Julia***. The package provides functions for generating long memory,
estimating the parameters of the models, and simulation. Generating
methods include fractional differencing, stochastic error duration, and
cross-sectional aggregation. Estimators include those inspired by the
log-periodogram regression and parametric ones. This notebook provides
an illustrative example on the use of the package.

# 1. Nile River minima data

## 1.1 Plotting the data, its autocorrelation function and spectral density

Loading the packages, if not installed, use the `Pkg.add()` function to
install them. `LongMemory.jl` includes plotting functions tailored for
long memory analysis. We use `Plots.jl` for additional plotting, and
`LongMemory.jl` for the long memory analysis.

In [1]:
using LongMemory, Plots

Data loading, and plot.

In [1]:
NileMin = NileData()
theme(:ggplot2)
p1 = plot( NileMin.Year , NileMin.NileMin, xlabel="Year" , ylabel = "Nile River minima" , legend = false )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip840)" d="M553.664 1463.7 Q550.053 1463.7 548.224 1467.26 Q546.418 1470.8 546.418 1477.93 Q546.418 1485.04 548.224 1488.61 Q550.053 1492.15 553.664 1492.15 Q557.298 1492.15 559.103 1488.61 Q560.932 1485.04 560.932 1477.93 Q560.932 1470.8 559.103 1467.26 Q557.298 1463.7 553.664 1463.7 M553.664 1459.99 Q559.474 1459.99 562.529 1464.6 Q565.608 1469.18 565.608 1477.93 Q565.608 1486.66 562.529 1491.27 Q559.474 1495.85 553.664 1495.85 Q547.853 1495.85 544.775 1491.27 Q541.719 1486.66 541.719 1477.93 Q541.719 1469.18 544.775 1464.6 Q547.853 1459.99 553.664 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip840)" d="M583.826 1463.7 Q580.214 1463.7 578.386 1467.26 Q576.58 1470.8 576.58 1477.93 Q576.58 1485.04 578.386 1488.61 Q580.214 1492.15 583.826 1492.15 Q587.46 1492.15 589.265 1488.61 Q591.094 1485.04 591.094 1477.93 Q591.094 1470.8 589.265 1467.26 Q587.46 1463.7 583.826 1463.7 M583.826 1459.99 Q589.636 1459.99 592.691 1464.6 Q595.77 1469.18 595.77 1477.93 Q595.77 1486.66 592.691 1491.27 Q589.636 1495.85 583.826 1495.85 Q578.015 1495.85 574.937 1491.27 Q571.881 1486.66 571.881 1477.93 Q571.881 1469.18 574.937 1464.6 Q578.015 1459.99 583.826 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip840)" d="M821.706 1478.77 Q818.373 1478.77 816.452 1480.55 Q814.553 1482.33 814.553 1485.46 Q814.553 1488.58 816.452 1490.37 Q818.373 1492.15 821.706 1492.15 Q825.04 1492.15 826.961 1490.37 Q828.882 1488.56 828.882 1485.46 Q828.882 1482.33 826.961 1480.55 Q825.063 1478.77 821.706 1478.77 M817.03 1476.78 Q814.021 1476.04 812.331 1473.98 Q810.665 1471.92 810.665 1468.95 Q810.665 1464.81 813.604 1462.4 Q816.567 1459.99 821.706 1459.99 Q826.868 1459.99 829.808 1462.4 Q832.748 1464.81 832.748 1468.95 Q832.748 1471.92 831.058 1473.98 Q829.391 1476.04 826.405 1476.78 Q829.785 1477.56 831.66 1479.86 Q833.558 1482.15 833.558 1485.46 Q833.558 1490.48 830.479 1493.17 Q827.424 1495.85 821.706 1495.85 Q815.989 1495.85 812.91 1493.17 Q809.854 1490.48 809.854 1485.46 Q809.854 1482.15 811.753 1479.86 Q813.651 1477.56 817.03 1476.78 M815.317 1469.39 Q815.317 1472.08 816.984 1473.58 Q818.674 1475.09 821.706 1475.09 Q824.715 1475.09 826.405 1473.58 Q828.118 1472.08 828.118 1469.39 Q828.118 1466.71 826.405 1465.2 Q824.715 1463.7 821.706 1463.7 Q818.674 1463.7 816.984 1465.2 Q815.317 1466.71 815.317 1469.39 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip840)" d="M851.868 1463.7 Q848.257 1463.7 846.428 1467.26 Q844.623 1470.8 844.623 1477.93 Q844.623 1485.04 846.428 1488.61 Q848.257 1492.15 851.868 1492.15 Q855.502 1492.15 857.308 1488.61 Q859.137 1485.04 859.137 1477.93 Q859.137 1470.8 857.308 1467.26 Q855.502 1463.7 851.868 1463.7 M851.868 1459.99 Q857.678 1459.99 860.734 1464.6 Q863.812 1469.18 863.812 1477.93 Q863.812 1486.66 860.734 1491.27 Q857.678 1495.85 851.868 1495.85 Q846.058 1495.85 842.979 1491.27 Q839.924 1486.66 839.924 1477.93 Q839.924 1469.18 842.979 1464.6 Q846.058 1459.99 851.868 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip840)" d="M882.03 1463.7 Q878.419 1463.7 876.59 1467.26 Q874.785 1470.8 874.785 1477.93 Q874.785 1485.04 876.59 1488.61 Q878.419 1492.15 882.03 1492.15 Q885.664 1492.15 887.47 1488.61 Q889.298 1485.04 889.298 1477.93 Q889.298 1470.8 887.47 1467.26 Q885.664 1463.7 882.03 1463.7 M882.03 1459.99 Q887.84 1459.99 890.896 1464.6 Q893.974 1469.18 893.974 1477.93 Q893.974 1486.66 890.896 1491.27 Q887.84 1495.85 882.03 1495.85 Q876.22 1495.85 873.141 1491.27 Q870.086 1486.66 870.086 1477.93 Q870.086 1469.18 873.141 1464.6 Q876.22 1459.99 882.03 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip840)" d="M1109.83 1494.46 L1109.83 1490.2 Q1111.59 1491.04 1113.39 14

Plotting the autocorrelation function using the `autocorrelation_plot()`
function from `LongMemory.jl`.

In [1]:
p2 = autocorrelation_plot(NileMin.NileMin, 50)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip900)" d="M268.574 1463.7 Q264.963 1463.7 263.134 1467.26 Q261.328 1470.8 261.328 1477.93 Q261.328 1485.04 263.134 1488.61 Q264.963 1492.15 268.574 1492.15 Q272.208 1492.15 274.014 1488.61 Q275.842 1485.04 275.842 1477.93 Q275.842 1470.8 274.014 1467.26 Q272.208 1463.7 268.574 1463.7 M268.574 1459.99 Q274.384 1459.99 277.44 1464.6 Q280.518 1469.18 280.518 1477.93 Q280.518 1486.66 277.44 1491.27 Q274.384 1495.85 268.574 1495.85 Q262.764 1495.85 259.685 1491.27 Q256.629 1486.66 256.629 1477.93 Q256.629 1469.18 259.685 1464.6 Q262.764 1459.99 268.574 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip900)" d="M687.545 1463.7 Q683.933 1463.7 682.105 1467.26 Q680.299 1470.8 680.299 1477.93 Q680.299 1485.04 682.105 1488.61 Q683.933 1492.15 687.545 1492.15 Q691.179 1492.15 692.984 1488.61 Q694.813 1485.04 694.813 1477.93 Q694.813 1470.8 692.984 1467.26 Q691.179 1463.7 687.545 1463.7 M687.545 1459.99 Q693.355 1459.99 696.41 1464.6 Q699.489 1469.18 699.489 1477.93 Q699.489 1486.66 696.41 1491.27 Q693.355 1495.85 687.545 1495.85 Q681.734 1495.85 678.656 1491.27 Q675.6 1486.66 675.6 1477.93 Q675.6 1469.18 678.656 1464.6 Q681.734 1459.99 687.545 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip900)" d="M1057.21 1491.24 L1073.53 1491.24 L1073.53 1495.18 L1051.58 1495.18 L1051.58 1491.24 Q1054.25 1488.49 1058.83 1483.86 Q1063.44 1479.21 1064.62 1477.87 Q1066.86 1475.34 1067.74 1473.61 Q1068.65 1471.85 1068.65 1470.16 Q1068.65 1467.4 1066.7 1465.67 Q1064.78 1463.93 1061.68 1463.93 Q1059.48 1463.93 1057.02 1464.69 Q1054.59 1465.46 1051.82 1467.01 L1051.82 1462.29 Q1054.64 1461.15 1057.09 1460.57 Q1059.55 1459.99 1061.58 1459.99 Q1066.96 1459.99 1070.15 1462.68 Q1073.34 1465.37 1073.34 1469.86 Q1073.34 1471.99 1072.53 1473.91 Q1071.75 1475.8 1069.64 1478.4 Q1069.06 1479.07 1065.96 1482.29 Q1062.86 1485.48 1057.21 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip900)" d="M1093.34 1463.7 Q1089.73 1463.7 1087.9 1467.26 Q1086.1 1470.8 1086.1 1477.93 Q1086.1 1485.04 1087.9 1488.61 Q1089.73 1492.15 1093.34 1492.15 Q1096.98 1492.15 1098.78 1488.61 Q1100.61 1485.04 1100.61 1477.93 Q1100.61 1470.8 1098.78 1467.26 Q1096.98 1463.7 1093.34 1463.7 M1093.34 1459.99 Q1099.15 1459.99 1102.21 1464.6 Q1105.29 1469.18 1105.29 1477.93 Q1105.29 1486.66 1102.21 1491.27 Q1099.15 1495.85 1093.34 1495.85 Q1087.53 1495.85 1084.46 1491.27 Q1081.4 1486.66 1081.4 1477.93 Q1081.4 1469.18 1084.46 1464.6 Q1087.53 1459.99 1093.34 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip900)" d="M1472.21 1476.55 Q1475.57 1477.26 1477.44 1479.53 Q1479.34 1481.8 1479.34 1485.13 Q1479.34 1490.25 1475.82 1493.05 Q1472.3 1495.85 1465.82 1495.85 Q1463.65 1495.85 1461.33 1495.41 Q1459.04 1494.99 1456.59 1494.14 L1456.59 1489.62 Q1458.53 1490.76 1460.85 1491.34 Q1463.16 1491.92 1465.68 1491.92 Q1470.08 1491.92 1472.37 1490.18 Q1474.69 1488.44 1474.69 1485.13 Q1474.69 1482.08 1472.53 1480.37 Q1470.41 1478.63 1466.59 1478.63 L1462.56 1478.63 L1462.56 1474.79 L1466.77 1474.79 Q1470.22 1474.79 1472.05 1473.42 Q1473.88 1472.03 1473.88 1469.44 Q1473.88 1466.78 1471.98 1465.37 Q1470.1 1463.93 1466.59 1463.93 Q1464.66 1463.93 1462.47 1464.35 Q1460.27 1464.76 1457.63 1465.64 L1457.63 1461.48 Q1460.29 1460.74 1462.6 1460.37 Q1464.94 1459.99 1467 1459.99 Q1472.33 1459.99 1475.43 1462.43 Q1478.53 1464.83 1478.53 1468.95 Q1478.53 1471.82 1476.89 1473.81 Q1475.24 1475.78 1472.21 1476.55 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip900)" d="M1498.21 1463.7 Q1494.59 1463.7 1492.77 1467.26 Q1490.96 1470.8 1490.96 1477.93 Q1490.96 1485.04 1492.77 1488.61 Q1494.59 1492.15 1498.21 1492.15 Q1501.84 1492.15 1503.65 1488.61 Q1505.47 1485.04 1505.47 1477

Plotting the spectral density with the *periodogram()* function.

In [1]:
p3 = periodogram_plot(NileMin.NileMin, slope = true)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip960)" d="M898.304 1476.55 Q901.661 1477.26 903.536 1479.53 Q905.434 1481.8 905.434 1485.13 Q905.434 1490.25 901.915 1493.05 Q898.397 1495.85 891.916 1495.85 Q889.74 1495.85 887.425 1495.41 Q885.133 1494.99 882.679 1494.14 L882.679 1489.62 Q884.624 1490.76 886.939 1491.34 Q889.254 1491.92 891.777 1491.92 Q896.175 1491.92 898.466 1490.18 Q900.781 1488.44 900.781 1485.13 Q900.781 1482.08 898.628 1480.37 Q896.499 1478.63 892.679 1478.63 L888.652 1478.63 L888.652 1474.79 L892.865 1474.79 Q896.314 1474.79 898.142 1473.42 Q899.971 1472.03 899.971 1469.44 Q899.971 1466.78 898.073 1465.37 Q896.198 1463.93 892.679 1463.93 Q890.758 1463.93 888.559 1464.35 Q886.36 1464.76 883.721 1465.64 L883.721 1461.48 Q886.383 1460.74 888.698 1460.37 Q891.036 1459.99 893.096 1459.99 Q898.42 1459.99 901.522 1462.43 Q904.624 1464.83 904.624 1468.95 Q904.624 1471.82 902.98 1473.81 Q901.337 1475.78 898.304 1476.55 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip960)" d="M1230.95 1491.24 L1247.27 1491.24 L1247.27 1495.18 L1225.33 1495.18 L1225.33 1491.24 Q1227.99 1488.49 1232.57 1483.86 Q1237.18 1479.21 1238.36 1477.87 Q1240.6 1475.34 1241.48 1473.61 Q1242.39 1471.85 1242.39 1470.16 Q1242.39 1467.4 1240.44 1465.67 Q1238.52 1463.93 1235.42 1463.93 Q1233.22 1463.93 1230.77 1464.69 Q1228.34 1465.46 1225.56 1467.01 L1225.56 1462.29 Q1228.38 1461.15 1230.84 1460.57 Q1233.29 1459.99 1235.33 1459.99 Q1240.7 1459.99 1243.89 1462.68 Q1247.09 1465.37 1247.09 1469.86 Q1247.09 1471.99 1246.28 1473.91 Q1245.49 1475.8 1243.38 1478.4 Q1242.8 1479.07 1239.7 1482.29 Q1236.6 1485.48 1230.95 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip960)" d="M1901.83 1463.7 Q1898.22 1463.7 1896.4 1467.26 Q1894.59 1470.8 1894.59 1477.93 Q1894.59 1485.04 1896.4 1488.61 Q1898.22 1492.15 1901.83 1492.15 Q1905.47 1492.15 1907.27 1488.61 Q1909.1 1485.04 1909.1 1477.93 Q1909.1 1470.8 1907.27 1467.26 Q1905.47 1463.7 1901.83 1463.7 M1901.83 1459.99 Q1907.65 1459.99 1910.7 1464.6 Q1913.78 1469.18 1913.78 1477.93 Q1913.78 1486.66 1910.7 1491.27 Q1907.65 1495.85 1901.83 1495.85 Q1896.02 1495.85 1892.95 1491.27 Q1889.89 1486.66 1889.89 1477.93 Q1889.89 1469.18 1892.95 1464.6 Q1896.02 1459.99 1901.83 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip960)" d="M1111.16 1536.5 Q1106.45 1536.5 1103.71 1540.19 Q1100.97 1543.85 1100.97 1550.25 Q1100.97 1556.65 1103.68 1560.34 Q1106.41 1564 1111.16 1564 Q1115.84 1564 1118.57 1560.31 Q1121.31 1556.62 1121.31 1550.25 Q1121.31 1543.92 1118.57 1540.23 Q1115.84 1536.5 1111.16 1536.5 M1111.16 1531.54 Q1118.8 1531.54 1123.16 1536.5 Q1127.52 1541.47 1127.52 1550.25 Q1127.52 1559 1123.16 1564 Q1118.8 1568.97 1111.16 1568.97 Q1103.49 1568.97 1099.13 1564 Q1094.8 1559 1094.8 1550.25 Q1094.8 1541.47 1099.13 1536.5 Q1103.49 1531.54 1111.16 1531.54 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip960)" d="M1160.68 1549.81 Q1160.68 1543.44 1158.04 1539.94 Q1155.43 1536.44 1150.69 1536.44 Q1145.98 1536.44 1143.34 1539.94 Q1140.73 1543.44 1140.73 1549.81 Q1140.73 1556.14 1143.34 1559.64 Q1145.98 1563.14 1150.69 1563.14 Q1155.43 1563.14 1158.04 1559.64 Q1160.68 1556.14 1160.68 1549.81 M1166.54 1563.62 Q1166.54 1572.72 1162.5 1577.15 Q1158.45 1581.6 1150.12 1581.6 Q1147.03 1581.6 1144.29 1581.13 Q1141.55 1580.68 1138.98 1579.72 L1138.98 1574.03 Q1141.55 1575.43 1144.07 1576.1 Q1146.58 1576.76 1149.19 1576.76 Q1154.95 1576.76 1157.82 1573.74 Q1160.68 1570.75 1160.68 1564.67 L1160.68 1561.77 Q1158.87 1564.92 1156.04 1566.48 Q1153.2 1568.04 1149.26 1568.04 Q1142.7 1568.04 1138.69 1563.05 Q1134.68 1558.05 1134.68 1549.81 Q1134.68 1541.53 1138.69 1536.53 Q1142.7 1531.54 1149.26 1531.54 Q1153.2 1531.54 1156.04 1533.1 Q1158.87 1534.66 1160.68 1537.81 L1160.68 153

Combining the plots.

In [1]:
l = @layout [a; b c]
theme(:ggplot2)
plot(p1, p2, p3, layout = l, size = (700, 500) )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip020)" d="M615.81 858.636 Q612.199 858.636 610.37 862.2 Q608.564 865.742 608.564 872.872 Q608.564 879.978 610.37 883.543 Q612.199 887.085 615.81 887.085 Q619.444 887.085 621.249 883.543 Q623.078 879.978 623.078 872.872 Q623.078 865.742 621.249 862.2 Q619.444 858.636 615.81 858.636 M615.81 854.932 Q621.62 854.932 624.675 859.538 Q627.754 864.122 627.754 872.872 Q627.754 881.599 624.675 886.205 Q621.62 890.788 615.81 890.788 Q610 890.788 606.921 886.205 Q603.865 881.599 603.865 872.872 Q603.865 864.122 606.921 859.538 Q610 854.932 615.81 854.932 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip020)" d="M645.972 858.636 Q642.36 858.636 640.532 862.2 Q638.726 865.742 638.726 872.872 Q638.726 879.978 640.532 883.543 Q642.36 887.085 645.972 887.085 Q649.606 887.085 651.411 883.543 Q653.24 879.978 653.24 872.872 Q653.24 865.742 651.411 862.2 Q649.606 858.636 645.972 858.636 M645.972 854.932 Q651.782 854.932 654.837 859.538 Q657.916 864.122 657.916 872.872 Q657.916 881.599 654.837 886.205 Q651.782 890.788 645.972 890.788 Q640.161 890.788 637.083 886.205 Q634.027 881.599 634.027 872.872 Q634.027 864.122 637.083 859.538 Q640.161 854.932 645.972 854.932 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip020)" d="M939.801 873.705 Q936.468 873.705 934.547 875.487 Q932.649 877.27 932.649 880.395 Q932.649 883.52 934.547 885.302 Q936.468 887.085 939.801 887.085 Q943.135 887.085 945.056 885.302 Q946.977 883.497 946.977 880.395 Q946.977 877.27 945.056 875.487 Q943.158 873.705 939.801 873.705 M935.125 871.714 Q932.116 870.974 930.426 868.913 Q928.76 866.853 928.76 863.89 Q928.76 859.747 931.699 857.339 Q934.662 854.932 939.801 854.932 Q944.963 854.932 947.903 857.339 Q950.843 859.747 950.843 863.89 Q950.843 866.853 949.153 868.913 Q947.486 870.974 944.5 871.714 Q947.88 872.501 949.755 874.793 Q951.653 877.085 951.653 880.395 Q951.653 885.418 948.574 888.103 Q945.519 890.788 939.801 890.788 Q934.084 890.788 931.005 888.103 Q927.949 885.418 927.949 880.395 Q927.949 877.085 929.848 874.793 Q931.746 872.501 935.125 871.714 M933.412 864.33 Q933.412 867.015 935.079 868.52 Q936.769 870.025 939.801 870.025 Q942.811 870.025 944.5 868.52 Q946.213 867.015 946.213 864.33 Q946.213 861.645 944.5 860.14 Q942.811 858.636 939.801 858.636 Q936.769 858.636 935.079 860.14 Q933.412 861.645 933.412 864.33 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip020)" d="M969.963 858.636 Q966.352 858.636 964.523 862.2 Q962.718 865.742 962.718 872.872 Q962.718 879.978 964.523 883.543 Q966.352 887.085 969.963 887.085 Q973.597 887.085 975.403 883.543 Q977.232 879.978 977.232 872.872 Q977.232 865.742 975.403 862.2 Q973.597 858.636 969.963 858.636 M969.963 854.932 Q975.773 854.932 978.829 859.538 Q981.908 864.122 981.908 872.872 Q981.908 881.599 978.829 886.205 Q975.773 890.788 969.963 890.788 Q964.153 890.788 961.074 886.205 Q958.019 881.599 958.019 872.872 Q958.019 864.122 961.074 859.538 Q964.153 854.932 969.963 854.932 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip020)" d="M1000.13 858.636 Q996.514 858.636 994.685 862.2 Q992.88 865.742 992.88 872.872 Q992.88 879.978 994.685 883.543 Q996.514 887.085 1000.13 887.085 Q1003.76 887.085 1005.56 883.543 Q1007.39 879.978 1007.39 872.872 Q1007.39 865.742 1005.56 862.2 Q1003.76 858.636 1000.13 858.636 M1000.13 854.932 Q1005.94 854.932 1008.99 859.538 Q1012.07 864.122 1012.07 872.872 Q1012.07 881.599 1008.99 886.205 Q1005.94 890.788 1000.13 890.788 Q994.315 890.788 991.236 886.205 Q988.181 881.599 988.181 872.872 Q988.181 864.122 991.236 859.538 Q994.315 854.932 1000.13 854.932 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip020)" d="M1283.87 889.399 L1283.87 885.14 Q1285.63 885.973 1287.44 

All the above plus the log-variance plot can be done in a single plot.

In [1]:
NileDataPlot()

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip080)" d="M387.222 657.557 Q383.611 657.557 381.782 661.122 Q379.977 664.663 379.977 671.793 Q379.977 678.899 381.782 682.464 Q383.611 686.006 387.222 686.006 Q390.856 686.006 392.662 682.464 Q394.49 678.899 394.49 671.793 Q394.49 664.663 392.662 661.122 Q390.856 657.557 387.222 657.557 M387.222 653.853 Q393.032 653.853 396.088 658.46 Q399.166 663.043 399.166 671.793 Q399.166 680.52 396.088 685.126 Q393.032 689.71 387.222 689.71 Q381.412 689.71 378.333 685.126 Q375.278 680.52 375.278 671.793 Q375.278 663.043 378.333 658.46 Q381.412 653.853 387.222 653.853 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M417.384 657.557 Q413.773 657.557 411.944 661.122 Q410.139 664.663 410.139 671.793 Q410.139 678.899 411.944 682.464 Q413.773 686.006 417.384 686.006 Q421.018 686.006 422.824 682.464 Q424.652 678.899 424.652 671.793 Q424.652 664.663 422.824 661.122 Q421.018 657.557 417.384 657.557 M417.384 653.853 Q423.194 653.853 426.25 658.46 Q429.328 663.043 429.328 671.793 Q429.328 680.52 426.25 685.126 Q423.194 689.71 417.384 689.71 Q411.574 689.71 408.495 685.126 Q405.439 680.52 405.439 671.793 Q405.439 663.043 408.495 658.46 Q411.574 653.853 417.384 653.853 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M485.183 672.626 Q481.85 672.626 479.928 674.409 Q478.03 676.191 478.03 679.316 Q478.03 682.441 479.928 684.223 Q481.85 686.006 485.183 686.006 Q488.516 686.006 490.438 684.223 Q492.359 682.418 492.359 679.316 Q492.359 676.191 490.438 674.409 Q488.54 672.626 485.183 672.626 M480.507 670.636 Q477.498 669.895 475.808 667.835 Q474.141 665.774 474.141 662.812 Q474.141 658.668 477.081 656.261 Q480.044 653.853 485.183 653.853 Q490.345 653.853 493.285 656.261 Q496.225 658.668 496.225 662.812 Q496.225 665.774 494.535 667.835 Q492.868 669.895 489.882 670.636 Q493.262 671.423 495.137 673.714 Q497.035 676.006 497.035 679.316 Q497.035 684.339 493.956 687.024 Q490.901 689.71 485.183 689.71 Q479.466 689.71 476.387 687.024 Q473.331 684.339 473.331 679.316 Q473.331 676.006 475.229 673.714 Q477.128 671.423 480.507 670.636 M478.794 663.251 Q478.794 665.937 480.461 667.441 Q482.151 668.946 485.183 668.946 Q488.192 668.946 489.882 667.441 Q491.595 665.937 491.595 663.251 Q491.595 660.566 489.882 659.062 Q488.192 657.557 485.183 657.557 Q482.151 657.557 480.461 659.062 Q478.794 660.566 478.794 663.251 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M515.345 657.557 Q511.734 657.557 509.905 661.122 Q508.1 664.663 508.1 671.793 Q508.1 678.899 509.905 682.464 Q511.734 686.006 515.345 686.006 Q518.979 686.006 520.785 682.464 Q522.613 678.899 522.613 671.793 Q522.613 664.663 520.785 661.122 Q518.979 657.557 515.345 657.557 M515.345 653.853 Q521.155 653.853 524.211 658.46 Q527.289 663.043 527.289 671.793 Q527.289 680.52 524.211 685.126 Q521.155 689.71 515.345 689.71 Q509.535 689.71 506.456 685.126 Q503.401 680.52 503.401 671.793 Q503.401 663.043 506.456 658.46 Q509.535 653.853 515.345 653.853 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M545.507 657.557 Q541.896 657.557 540.067 661.122 Q538.261 664.663 538.261 671.793 Q538.261 678.899 540.067 682.464 Q541.896 686.006 545.507 686.006 Q549.141 686.006 550.947 682.464 Q552.775 678.899 552.775 671.793 Q552.775 664.663 550.947 661.122 Q549.141 657.557 545.507 657.557 M545.507 653.853 Q551.317 653.853 554.373 658.46 Q557.451 663.043 557.451 671.793 Q557.451 680.52 554.373 685.126 Q551.317 689.71 545.507 689.71 Q539.697 689.71 536.618 685.126 Q533.562 680.52 533.562 671.793 Q533.562 663.043 536.618 658.46 Q539.697 653.853 545.507 653.853 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip080)" d="M603.225 688.321 L603.225 684.061 Q604.984

# 2. Long memory generation

## 2.1 Fractional differencing generation and plotting

Loading the package for random number generation, setting the seed, and
generating the fractional differenced series using the *fi_gen()*
function.

In [1]:
using Random
Random.seed!(1234)

dx = fi_gen(500, 0.3)

500-element Vector{Float64}:
  0.9706563288552144
 -0.6880215128786353
  0.7973733442603004
  0.19192066674807973
 -0.46144511739243654
 -1.514799781765257
  2.250125601629064
  2.0467649947720434
  1.5280686228970999
 -0.12693052530986765
  ⋮
 -0.930134105560699
 -1.333219179460856
 -0.49678208289873016
 -1.0341442518867012
 -1.0834385445422625
 -1.0557333271693794
 -0.08535062227423565
 -1.783593060065521
  0.11117399279145967

Plotting the fractional differenced series, and the sample
autocorrelation function. The theoretical autocorrelation function is
also plotted by using the `fi_var_vals()` function.

In [1]:
p1 = plot( dx , label = "Fractionally differenced data" )
p2 = plot( 0:50 , autocorrelation( dx , 51 ) , label = "Sample autocorrelation function", line = :stem , marker = :circle)
plot!( 0:50, fi_cor_vals( 51, 0.3 ), linewidth = 2, line = :dash, label = "Theoretical autocorrelation function")
l = @layout [a b]
theme(:ggplot2)
plot(p1, p2, layout = l, size = (700, 250) )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip140)" d="M184.383 953.812 Q180.772 953.812 178.943 957.377 Q177.138 960.919 177.138 968.048 Q177.138 975.155 178.943 978.72 Q180.772 982.261 184.383 982.261 Q188.017 982.261 189.823 978.72 Q191.652 975.155 191.652 968.048 Q191.652 960.919 189.823 957.377 Q188.017 953.812 184.383 953.812 M184.383 950.109 Q190.193 950.109 193.249 954.715 Q196.328 959.298 196.328 968.048 Q196.328 976.775 193.249 981.382 Q190.193 985.965 184.383 985.965 Q178.573 985.965 175.494 981.382 Q172.439 976.775 172.439 968.048 Q172.439 959.298 175.494 954.715 Q178.573 950.109 184.383 950.109 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip140)" d="M406.623 953.812 Q403.012 953.812 401.183 957.377 Q399.377 960.919 399.377 968.048 Q399.377 975.155 401.183 978.72 Q403.012 982.261 406.623 982.261 Q410.257 982.261 412.063 978.72 Q413.891 975.155 413.891 968.048 Q413.891 960.919 412.063 957.377 Q410.257 953.812 406.623 953.812 M406.623 950.109 Q412.433 950.109 415.488 954.715 Q418.567 959.298 418.567 968.048 Q418.567 976.775 415.488 981.382 Q412.433 985.965 406.623 985.965 Q400.813 985.965 397.734 981.382 Q394.678 976.775 394.678 968.048 Q394.678 959.298 397.734 954.715 Q400.813 950.109 406.623 950.109 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip140)" d="M436.785 953.812 Q433.174 953.812 431.345 957.377 Q429.539 960.919 429.539 968.048 Q429.539 975.155 431.345 978.72 Q433.174 982.261 436.785 982.261 Q440.419 982.261 442.224 978.72 Q444.053 975.155 444.053 968.048 Q444.053 960.919 442.224 957.377 Q440.419 953.812 436.785 953.812 M436.785 950.109 Q442.595 950.109 445.65 954.715 Q448.729 959.298 448.729 968.048 Q448.729 976.775 445.65 981.382 Q442.595 985.965 436.785 985.965 Q430.974 985.965 427.896 981.382 Q424.84 976.775 424.84 968.048 Q424.84 959.298 427.896 954.715 Q430.974 950.109 436.785 950.109 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip140)" d="M594.638 981.358 L610.957 981.358 L610.957 985.294 L589.013 985.294 L589.013 981.358 Q591.675 978.604 596.258 973.974 Q600.865 969.321 602.045 967.979 Q604.291 965.456 605.17 963.72 Q606.073 961.96 606.073 960.271 Q606.073 957.516 604.129 955.78 Q602.207 954.044 599.105 954.044 Q596.906 954.044 594.453 954.808 Q592.022 955.572 589.244 957.122 L589.244 952.4 Q592.069 951.266 594.522 950.687 Q596.976 950.109 599.013 950.109 Q604.383 950.109 607.578 952.794 Q610.772 955.479 610.772 959.97 Q610.772 962.099 609.962 964.021 Q609.175 965.919 607.068 968.511 Q606.49 969.183 603.388 972.4 Q600.286 975.595 594.638 981.358 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip140)" d="M630.772 953.812 Q627.161 953.812 625.332 957.377 Q623.527 960.919 623.527 968.048 Q623.527 975.155 625.332 978.72 Q627.161 982.261 630.772 982.261 Q634.406 982.261 636.212 978.72 Q638.04 975.155 638.04 968.048 Q638.04 960.919 636.212 957.377 Q634.406 953.812 630.772 953.812 M630.772 950.109 Q636.582 950.109 639.638 954.715 Q642.716 959.298 642.716 968.048 Q642.716 976.775 639.638 981.382 Q636.582 985.965 630.772 985.965 Q624.962 985.965 621.883 981.382 Q618.828 976.775 618.828 968.048 Q618.828 959.298 621.883 954.715 Q624.962 950.109 630.772 950.109 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip140)" d="M660.934 953.812 Q657.323 953.812 655.494 957.377 Q653.689 960.919 653.689 968.048 Q653.689 975.155 655.494 978.72 Q657.323 982.261 660.934 982.261 Q664.568 982.261 666.374 978.72 Q668.202 975.155 668.202 968.048 Q668.202 960.919 666.374 957.377 Q664.568 953.812 660.934 953.812 M660.934 950.109 Q666.744 950.109 669.8 954.715 Q672.878 959.298 672.878 968.048 Q672.878 976.775 669.8 981.382 Q666.744 985.965 660.934 985.965 Q655.124 985.965 652.045 981.382 Q648.989 976.775 648.989 968.048 Q648.989 959.298 652.045 

## 2.2 Cross-sectional aggregation generation and plotting

Generating the cross-sectional aggregation series using the `csa_gen()`
function.

Multiple dispatch is used to generate the series. The finite
approximation is used if we define the first two arguments as the sample
size and the number of series. The asymptotic version is used if the
number of series to use is not passed to the function. The final two
arguments are the parameters of the Beta function.

In [1]:
csa_fin = csa_gen(1000,1000,1.3,1.5)
csa_asym = csa_gen(1000,1.3,1.5)

1000-element Vector{Float64}:
  1.6030252183868878
  0.8573306416834465
  1.5303712736128772
 -0.7891472078980322
 -0.882765121556601
  0.08140313409601763
  0.19004851299411052
  0.8054252402927868
  1.9809498685219085
  0.5463250128619025
  ⋮
  1.885482132160916
  3.3979888982746855
  1.8613002384806776
  2.1740032426543214
  1.15009413905651
  2.445556824444752
  2.2321630950017806
  2.081473846697694
  2.044650720085682

Plotting the autocorrelation function of the finite and asymptotic
series. The theoretical autocorrelation function is also plotted by
using the `csa_var_vals()` function.

In [1]:
plot( 0:50 , autocorrelation( csa_fin , 51 ) , label = "Sample autocorrelation function, finite approximation", line = :stem , marker = :circle)
plot!( 0:50 , autocorrelation( csa_asym , 51 ) , label = "Sample autocorrelation function, asymptotic model", line = :stem , marker = :circle, color = :black)
plot!( 0:50, csa_cor_vals( 51, 1.3, 1.5 ), linewidth = 3, line = :dash, label = "Theoretical autocorrelation function", color = :red)
theme(:ggplot2)
plot!(size = (500, 200) )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip200)" d="M232.382 743.991 Q228.771 743.991 226.942 747.555 Q225.137 751.097 225.137 758.227 Q225.137 765.333 226.942 768.898 Q228.771 772.439 232.382 772.439 Q236.016 772.439 237.822 768.898 Q239.65 765.333 239.65 758.227 Q239.65 751.097 237.822 747.555 Q236.016 743.991 232.382 743.991 M232.382 740.287 Q238.192 740.287 241.248 744.893 Q244.326 749.477 244.326 758.227 Q244.326 766.953 241.248 771.56 Q238.192 776.143 232.382 776.143 Q226.572 776.143 223.493 771.56 Q220.438 766.953 220.438 758.227 Q220.438 749.477 223.493 744.893 Q226.572 740.287 232.382 740.287 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip200)" d="M580.474 743.991 Q576.863 743.991 575.035 747.555 Q573.229 751.097 573.229 758.227 Q573.229 765.333 575.035 768.898 Q576.863 772.439 580.474 772.439 Q584.109 772.439 585.914 768.898 Q587.743 765.333 587.743 758.227 Q587.743 751.097 585.914 747.555 Q584.109 743.991 580.474 743.991 M580.474 740.287 Q586.285 740.287 589.34 744.893 Q592.419 749.477 592.419 758.227 Q592.419 766.953 589.34 771.56 Q586.285 776.143 580.474 776.143 Q574.664 776.143 571.586 771.56 Q568.53 766.953 568.53 758.227 Q568.53 749.477 571.586 744.893 Q574.664 740.287 580.474 740.287 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip200)" d="M879.262 771.537 L895.581 771.537 L895.581 775.472 L873.637 775.472 L873.637 771.537 Q876.299 768.782 880.882 764.152 Q885.488 759.5 886.669 758.157 Q888.914 755.634 889.794 753.898 Q890.697 752.139 890.697 750.449 Q890.697 747.694 888.752 745.958 Q886.831 744.222 883.729 744.222 Q881.53 744.222 879.076 744.986 Q876.646 745.75 873.868 747.301 L873.868 742.579 Q876.692 741.444 879.146 740.866 Q881.6 740.287 883.637 740.287 Q889.007 740.287 892.201 742.972 Q895.396 745.657 895.396 750.148 Q895.396 752.278 894.586 754.199 Q893.799 756.097 891.692 758.69 Q891.113 759.361 888.012 762.578 Q884.91 765.773 879.262 771.537 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip200)" d="M915.396 743.991 Q911.785 743.991 909.956 747.555 Q908.15 751.097 908.15 758.227 Q908.15 765.333 909.956 768.898 Q911.785 772.439 915.396 772.439 Q919.03 772.439 920.835 768.898 Q922.664 765.333 922.664 758.227 Q922.664 751.097 920.835 747.555 Q919.03 743.991 915.396 743.991 M915.396 740.287 Q921.206 740.287 924.261 744.893 Q927.34 749.477 927.34 758.227 Q927.34 766.953 924.261 771.56 Q921.206 776.143 915.396 776.143 Q909.586 776.143 906.507 771.56 Q903.451 766.953 903.451 758.227 Q903.451 749.477 906.507 744.893 Q909.586 740.287 915.396 740.287 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip200)" d="M1223.38 756.838 Q1226.74 757.555 1228.62 759.824 Q1230.51 762.092 1230.51 765.426 Q1230.51 770.541 1227 773.342 Q1223.48 776.143 1217 776.143 Q1214.82 776.143 1212.5 775.703 Q1210.21 775.287 1207.76 774.43 L1207.76 769.916 Q1209.7 771.051 1212.02 771.629 Q1214.33 772.208 1216.86 772.208 Q1221.25 772.208 1223.55 770.472 Q1225.86 768.736 1225.86 765.426 Q1225.86 762.37 1223.71 760.657 Q1221.58 758.921 1217.76 758.921 L1213.73 758.921 L1213.73 755.078 L1217.94 755.078 Q1221.39 755.078 1223.22 753.713 Q1225.05 752.324 1225.05 749.731 Q1225.05 747.069 1223.15 745.657 Q1221.28 744.222 1217.76 744.222 Q1215.84 744.222 1213.64 744.639 Q1211.44 745.055 1208.8 745.935 L1208.8 741.768 Q1211.46 741.028 1213.78 740.657 Q1216.12 740.287 1218.18 740.287 Q1223.5 740.287 1226.6 742.717 Q1229.7 745.125 1229.7 749.245 Q1229.7 752.116 1228.06 754.106 Q1226.42 756.074 1223.38 756.838 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip200)" d="M1249.38 743.991 Q1245.77 743.991 1243.94 747.555 Q1242.13 751.097 1242.13 758.227 Q1242.13 765.333 1243.94 768.898 Q1245.77 772.439 1249.38 772.439 Q1253.01 772.439 1254.82 768.898 Q1256.65 765.333 125

## 2.3 Stochastic duration shocks generation and plotting

Data generation and plotting. We use the `sds_gen()` function to
generate the data, and the `LMPlot()` function to plot it along with
three diagnostic plots.

In [1]:
LMPlot(sds_gen(1000,0.45), name = "Stochastic duration shock")
theme(:ggplot2)
plot!( size = (700, 500) )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip260)" d="M288.676 852.055 Q285.065 852.055 283.236 855.62 Q281.431 859.162 281.431 866.291 Q281.431 873.398 283.236 876.963 Q285.065 880.504 288.676 880.504 Q292.31 880.504 294.116 876.963 Q295.945 873.398 295.945 866.291 Q295.945 859.162 294.116 855.62 Q292.31 852.055 288.676 852.055 M288.676 848.352 Q294.486 848.352 297.542 852.958 Q300.621 857.541 300.621 866.291 Q300.621 875.018 297.542 879.625 Q294.486 884.208 288.676 884.208 Q282.866 884.208 279.787 879.625 Q276.732 875.018 276.732 866.291 Q276.732 857.541 279.787 852.958 Q282.866 848.352 288.676 848.352 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip260)" d="M591.832 848.977 L610.189 848.977 L610.189 852.912 L596.115 852.912 L596.115 861.384 Q597.133 861.037 598.152 860.875 Q599.17 860.69 600.189 860.69 Q605.976 860.69 609.355 863.861 Q612.735 867.032 612.735 872.449 Q612.735 878.027 609.263 881.129 Q605.79 884.208 599.471 884.208 Q597.295 884.208 595.027 883.838 Q592.781 883.467 590.374 882.727 L590.374 878.027 Q592.457 879.162 594.679 879.717 Q596.902 880.273 599.378 880.273 Q603.383 880.273 605.721 878.166 Q608.059 876.06 608.059 872.449 Q608.059 868.838 605.721 866.731 Q603.383 864.625 599.378 864.625 Q597.504 864.625 595.629 865.041 Q593.777 865.458 591.832 866.338 L591.832 848.977 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip260)" d="M631.948 852.055 Q628.337 852.055 626.508 855.62 Q624.702 859.162 624.702 866.291 Q624.702 873.398 626.508 876.963 Q628.337 880.504 631.948 880.504 Q635.582 880.504 637.388 876.963 Q639.216 873.398 639.216 866.291 Q639.216 859.162 637.388 855.62 Q635.582 852.055 631.948 852.055 M631.948 848.352 Q637.758 848.352 640.813 852.958 Q643.892 857.541 643.892 866.291 Q643.892 875.018 640.813 879.625 Q637.758 884.208 631.948 884.208 Q626.138 884.208 623.059 879.625 Q620.003 875.018 620.003 866.291 Q620.003 857.541 623.059 852.958 Q626.138 848.352 631.948 848.352 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip260)" d="M662.11 852.055 Q658.499 852.055 656.67 855.62 Q654.864 859.162 654.864 866.291 Q654.864 873.398 656.67 876.963 Q658.499 880.504 662.11 880.504 Q665.744 880.504 667.549 876.963 Q669.378 873.398 669.378 866.291 Q669.378 859.162 667.549 855.62 Q665.744 852.055 662.11 852.055 M662.11 848.352 Q667.92 848.352 670.975 852.958 Q674.054 857.541 674.054 866.291 Q674.054 875.018 670.975 879.625 Q667.92 884.208 662.11 884.208 Q656.299 884.208 653.221 879.625 Q650.165 875.018 650.165 866.291 Q650.165 857.541 653.221 852.958 Q656.299 848.352 662.11 848.352 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip260)" d="M959.629 852.055 Q956.018 852.055 954.189 855.62 Q952.384 859.162 952.384 866.291 Q952.384 873.398 954.189 876.963 Q956.018 880.504 959.629 880.504 Q963.263 880.504 965.069 876.963 Q966.898 873.398 966.898 866.291 Q966.898 859.162 965.069 855.62 Q963.263 852.055 959.629 852.055 M959.629 848.352 Q965.439 848.352 968.495 852.958 Q971.573 857.541 971.573 866.291 Q971.573 875.018 968.495 879.625 Q965.439 884.208 959.629 884.208 Q953.819 884.208 950.74 879.625 Q947.685 875.018 947.685 866.291 Q947.685 857.541 950.74 852.958 Q953.819 848.352 959.629 848.352 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip260)" d="M989.791 852.055 Q986.18 852.055 984.351 855.62 Q982.546 859.162 982.546 866.291 Q982.546 873.398 984.351 876.963 Q986.18 880.504 989.791 880.504 Q993.425 880.504 995.231 876.963 Q997.059 873.398 997.059 866.291 Q997.059 859.162 995.231 855.62 Q993.425 852.055 989.791 852.055 M989.791 848.352 Q995.601 848.352 998.657 852.958 Q1001.74 857.541 1001.74 866.291 Q1001.74 875.018 998.657 879.625 Q995.601 884.208 989.791 884.208 Q983.981 884.208 980.902 879.625 Q977.847 875.018 977.847 866.291 Q977.847 857.541 9

# 3. Long memory estimation

## 3.1 Classic estimators

### 3.1.1 Variance plot in Nile River data

The variance plot is computed by the `log_variance_plot()` function. The
number of subsamples to use is passed to the function as the `m`
argument. The `slope` and `slope2` arguments are used to plot the
theoretical and estimated slopes, respectively.

In [1]:
log_variance_plot( NileData().NileMin; m=300, slope = true, slope2 = true )
plot!(size = (500, 300) )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip320)" d="M569.886 1098.65 L586.205 1098.65 L586.205 1102.59 L564.261 1102.59 L564.261 1098.65 Q566.923 1095.9 571.506 1091.27 Q576.113 1086.62 577.293 1085.27 Q579.539 1082.75 580.418 1081.01 Q581.321 1079.25 581.321 1077.56 Q581.321 1074.81 579.377 1073.07 Q577.455 1071.34 574.353 1071.34 Q572.154 1071.34 569.701 1072.1 Q567.27 1072.87 564.492 1074.42 L564.492 1069.69 Q567.316 1068.56 569.77 1067.98 Q572.224 1067.4 574.261 1067.4 Q579.631 1067.4 582.826 1070.09 Q586.02 1072.77 586.02 1077.26 Q586.02 1079.39 585.21 1081.31 Q584.423 1083.21 582.316 1085.81 Q581.738 1086.48 578.636 1089.69 Q575.534 1092.89 569.886 1098.65 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M929.374 1083.95 Q932.73 1084.67 934.605 1086.94 Q936.504 1089.21 936.504 1092.54 Q936.504 1097.66 932.985 1100.46 Q929.467 1103.26 922.985 1103.26 Q920.809 1103.26 918.494 1102.82 Q916.203 1102.4 913.749 1101.55 L913.749 1097.03 Q915.693 1098.17 918.008 1098.75 Q920.323 1099.32 922.846 1099.32 Q927.244 1099.32 929.536 1097.59 Q931.851 1095.85 931.851 1092.54 Q931.851 1089.49 929.698 1087.77 Q927.568 1086.04 923.749 1086.04 L919.721 1086.04 L919.721 1082.19 L923.934 1082.19 Q927.383 1082.19 929.212 1080.83 Q931.041 1079.44 931.041 1076.85 Q931.041 1074.19 929.142 1072.77 Q927.267 1071.34 923.749 1071.34 Q921.828 1071.34 919.629 1071.75 Q917.43 1072.17 914.791 1073.05 L914.791 1068.88 Q917.453 1068.14 919.767 1067.77 Q922.105 1067.4 924.166 1067.4 Q929.49 1067.4 932.592 1069.83 Q935.693 1072.24 935.693 1076.36 Q935.693 1079.23 934.05 1081.22 Q932.406 1083.19 929.374 1083.95 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip320)" d="M1615.19 1068.03 L1633.55 1068.03 L1633.55 1071.96 L1619.47 1071.96 L1619.47 1080.44 Q1620.49 1080.09 1621.51 1079.93 Q1622.53 1079.74 1623.55 1079.74 Q1629.33 1079.74 1632.71 1082.91 Q1636.09 1086.08 1636.09 1091.5 Q1636.09 1097.08 1632.62 1100.18 Q1629.15 1103.26 1622.83 1103.26 Q1620.65 1103.26 1618.38 1102.89 Q1616.14 1102.52 1613.73 1101.78 L1613.73 1097.08 Q1615.82 1098.21 1618.04 1098.77 Q1620.26 1099.32 1622.74 1099.32 Q1626.74 1099.32 1629.08 1097.22 Q1631.42 1095.11 1631.42 1091.5 Q1631.42 1087.89 1629.08 1085.78 Q1626.74 1083.68 1622.74 1083.68 Q1620.86 1083.68 1618.99 1084.09 Q1617.13 1084.51 1615.19 1085.39 L1615.19 1068.03 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip320)" d="M909.31 1142.71 Q904.6 1142.71 901.862 1146.4 Q899.125 1150.06 899.125 1156.46 Q899.125 1162.86 901.83 1166.55 Q904.568 1170.21 909.31 1170.21 Q913.989 1170.21 916.726 1166.52 Q919.463 1162.83 919.463 1156.46 Q919.463 1150.13 916.726 1146.43 Q913.989 1142.71 909.31 1142.71 M909.31 1137.74 Q916.949 1137.74 921.309 1142.71 Q925.67 1147.68 925.67 1156.46 Q925.67 1165.21 921.309 1170.21 Q916.949 1175.17 909.31 1175.17 Q901.639 1175.17 897.279 1170.21 Q892.95 1165.21 892.95 1156.46 Q892.95 1147.68 897.279 1142.71 Q901.639 1137.74 909.31 1137.74 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip320)" d="M958.835 1156.01 Q958.835 1149.65 956.194 1146.15 Q953.584 1142.65 948.841 1142.65 Q944.131 1142.65 941.489 1146.15 Q938.879 1149.65 938.879 1156.01 Q938.879 1162.35 941.489 1165.85 Q944.131 1169.35 948.841 1169.35 Q953.584 1169.35 956.194 1165.85 Q958.835 1162.35 958.835 1156.01 M964.692 1169.83 Q964.692 1178.93 960.65 1183.35 Q956.607 1187.81 948.268 1187.81 Q945.181 1187.81 942.444 1187.33 Q939.706 1186.89 937.128 1185.93 L937.128 1180.24 Q939.706 1181.64 942.221 1182.3 Q944.735 1182.97 947.345 1182.97 Q953.106 1182.97 955.971 1179.95 Q958.835 1176.96 958.835 1170.88 L958.835 1167.98 Q957.021 1171.13 954.188 1172.69 Q951.356 1174.25 947.409 1174.25 Q940.852 1174.25 936.842 1169.25 Q932.831 1164.26 932.831 1156.01 Q932.831 1147.74 936.842 11

Computing the long memory parameter by the log-variance plot.

In [1]:
log_variance_est( NileData().NileMin; m=300 )

0.15619757726603745

### 3.1.2 Rescaled range analysis in Nile River data

Estimation by the rescaled range, $R/S$. The number of subsamples to use
is passed to the function as the `k` argument.

In [1]:
rescaled_range_est( NileData().NileMin; k = 300 )

0.42546060138176556

Rescaled range plot. The number of subsamples to use is passed to the
function as the `k` argument. The `slope` and `slope2` arguments are
used to plot the theoretical and estimated slopes, respectively.

In [1]:
rescaled_range_plot( NileData().NileMin; k = 300, slope = true, slope2 = true )

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip380)" d="M574.709 1491.24 L591.028 1491.24 L591.028 1495.18 L569.084 1495.18 L569.084 1491.24 Q571.746 1488.49 576.329 1483.86 Q580.936 1479.21 582.116 1477.87 Q584.362 1475.34 585.241 1473.61 Q586.144 1471.85 586.144 1470.16 Q586.144 1467.4 584.2 1465.67 Q582.278 1463.93 579.177 1463.93 Q576.978 1463.93 574.524 1464.69 Q572.093 1465.46 569.316 1467.01 L569.316 1462.29 Q572.14 1461.15 574.593 1460.57 Q577.047 1459.99 579.084 1459.99 Q584.454 1459.99 587.649 1462.68 Q590.843 1465.37 590.843 1469.86 Q590.843 1471.99 590.033 1473.91 Q589.246 1475.8 587.14 1478.4 Q586.561 1479.07 583.459 1482.29 Q580.357 1485.48 574.709 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M964.816 1476.55 Q968.173 1477.26 970.048 1479.53 Q971.946 1481.8 971.946 1485.13 Q971.946 1490.25 968.427 1493.05 Q964.909 1495.85 958.427 1495.85 Q956.251 1495.85 953.936 1495.41 Q951.645 1494.99 949.191 1494.14 L949.191 1489.62 Q951.136 1490.76 953.45 1491.34 Q955.765 1491.92 958.288 1491.92 Q962.686 1491.92 964.978 1490.18 Q967.293 1488.44 967.293 1485.13 Q967.293 1482.08 965.14 1480.37 Q963.011 1478.63 959.191 1478.63 L955.163 1478.63 L955.163 1474.79 L959.376 1474.79 Q962.825 1474.79 964.654 1473.42 Q966.483 1472.03 966.483 1469.44 Q966.483 1466.78 964.585 1465.37 Q962.71 1463.93 959.191 1463.93 Q957.27 1463.93 955.071 1464.35 Q952.872 1464.76 950.233 1465.64 L950.233 1461.48 Q952.895 1460.74 955.21 1460.37 Q957.548 1459.99 959.608 1459.99 Q964.932 1459.99 968.034 1462.43 Q971.135 1464.83 971.135 1468.95 Q971.135 1471.82 969.492 1473.81 Q967.848 1475.78 964.816 1476.55 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip380)" d="M1711.87 1460.62 L1730.23 1460.62 L1730.23 1464.56 L1716.15 1464.56 L1716.15 1473.03 Q1717.17 1472.68 1718.19 1472.52 Q1719.21 1472.33 1720.23 1472.33 Q1726.01 1472.33 1729.39 1475.5 Q1732.77 1478.68 1732.77 1484.09 Q1732.77 1489.67 1729.3 1492.77 Q1725.83 1495.85 1719.51 1495.85 Q1717.33 1495.85 1715.07 1495.48 Q1712.82 1495.11 1710.41 1494.37 L1710.41 1489.67 Q1712.5 1490.8 1714.72 1491.36 Q1716.94 1491.92 1719.42 1491.92 Q1723.42 1491.92 1725.76 1489.81 Q1728.1 1487.7 1728.1 1484.09 Q1728.1 1480.48 1725.76 1478.37 Q1723.42 1476.27 1719.42 1476.27 Q1717.54 1476.27 1715.67 1476.68 Q1713.82 1477.1 1711.87 1477.98 L1711.87 1460.62 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip380)" d="M2102.51 1476.04 Q2099.36 1476.04 2097.51 1478.19 Q2095.68 1480.34 2095.68 1484.09 Q2095.68 1487.82 2097.51 1489.99 Q2099.36 1492.15 2102.51 1492.15 Q2105.66 1492.15 2107.49 1489.99 Q2109.34 1487.82 2109.34 1484.09 Q2109.34 1480.34 2107.49 1478.19 Q2105.66 1476.04 2102.51 1476.04 M2111.79 1461.38 L2111.79 1465.64 Q2110.03 1464.81 2108.23 1464.37 Q2106.45 1463.93 2104.69 1463.93 Q2100.06 1463.93 2097.6 1467.05 Q2095.17 1470.18 2094.82 1476.5 Q2096.19 1474.49 2098.25 1473.42 Q2100.31 1472.33 2102.79 1472.33 Q2108 1472.33 2111.01 1475.5 Q2114.04 1478.65 2114.04 1484.09 Q2114.04 1489.42 2110.89 1492.63 Q2107.74 1495.85 2102.51 1495.85 Q2096.51 1495.85 2093.34 1491.27 Q2090.17 1486.66 2090.17 1477.93 Q2090.17 1469.74 2094.06 1464.88 Q2097.95 1459.99 2104.5 1459.99 Q2106.26 1459.99 2108.04 1460.34 Q2109.85 1460.69 2111.79 1461.38 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip380)" d="M1091.76 1536.5 Q1087.05 1536.5 1084.32 1540.19 Q1081.58 1543.85 1081.58 1550.25 Q1081.58 1556.65 1084.29 1560.34 Q1087.02 1564 1091.76 1564 Q1096.44 1564 1099.18 1560.31 Q1101.92 1556.62 1101.92 1550.25 Q1101.92 1543.92 1099.18 1540.23 Q1096.44 1536.5 1091.76 1536.5 M1091.76 1531.54 Q1099.4 1531.54 1103.76 1536.5 Q1108.12 1541.47 1108.12 1550.25 Q1108.12 1559 1103.76 1564 Q1099.4 1568.97 1091.76 1568.97 Q1084.09 1568.97 1079.73 1564 Q1075.41 1559 1075.41 1550

## 3.2 Semiparametric estimators

### 3.2.1 Log-periodogram regression in Nile River data

GPH and bias-reduced estimator with one polynomial term. The number of
polynomial terms is passed to the function as the `br` argument. If not
passed, the function uses the default value of 0, recovering the GPH
estimator.

In [1]:
(gph_est( NileData().NileMin ),  gph_est( NileData().NileMin ; br = 1))

(0.3744941050542384, 0.397455265935833)

Variance estimates using the data.

In [1]:
(gph_est_variance( NileData().NileMin ),  gph_est_variance( NileData().NileMin ; br = 1))

(0.002272008379624622, 0.0051120188541553995)

Variance estimates using multiple dispatch on the sample size.

In [1]:
(gph_est_variance( length( NileData().NileMin ) ),  gph_est_variance( length( NileData().NileMin ) ; br = 1))

(0.002272008379624622, 0.0051120188541553995)

### 3.2.2 (Exact) Local Whittle estimator in Nile River data

The local Whittle and exact local Whittle estimators are computed by the
`whittle_est()` and `exact_whittle_est()` functions, respectively.

In [1]:
(whittle_est( NileData().NileMin ),  exact_whittle_est( NileData().NileMin ))

(0.37635955766434004, 0.40884952395694235)

Variance estimates using the data.

In [1]:
(whittle_est_variance( NileData().NileMin ),  exact_whittle_est_variance( NileData().NileMin ))

(0.0013812154696132596, 0.0013812154696132596)

## 3.3 Parametric estimators

### 3.3.1 Fractional differencing MLE in Nile River data

The fractional differencing MLE is computed by the `fi_mle_est()`
function. The function returns the estimated fractional differencing
parameter and the estimated standard error in a tuple.

In [1]:
dmle, sigfi = fi_mle_est( NileData().NileMin )

(0.39257149939646996, 69.95632676539788)

### 3.3.2 CSA MLE in Nile River data

The MLE for the cross-sectionally aggregated process is computed by the
`csa_mle_est()` function. The function returns the estimated parameters
of the Beta distribution, and the estimated standard error in a tuple.

In [1]:
pmle, qmle, sigcsa = csa_mle_est( NileData().NileMin )

(1.000001198981061, 2.447941980497643, 106.80313057162732)

### 3.3.3 Custom-HAR in Nile River data

A custom HAR model can be estimated by the function `har_est()`. The
lags for the custom HAR model are passed as an array to the function as
the `m` argument. The function returns the estimated parameters of the
model, and the estimated standard error in a tuple.

In [1]:
beta_har, sighar = har_est( NileData().NileMin; m = [1, 7] )

([254.23541690816782, 0.40096895301134383, 0.377482428389991], 69.6124509836161)

# 4. Long memory forecasting

## 4.1 Forecasting the Nile River minima data

### 4.1.1 Fractional differencing forecasting

The `fi_forecast_()` function returns the forecasted values, while the
`fi_forecast_plot()` functions returns the plot. First argument is the
time series to forecast. The second and third arguments are used to
define the number of steps ahead to forecast and the long memory
parameter. The optional fourth argument is used to define the standard
deviation to plot the confidence bands.

In [1]:
p1 = fi_forecast_plot( NileData().NileMin , 30, dmle, sigfi)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip440)" d="M328.341 1463.7 Q324.73 1463.7 322.901 1467.26 Q321.096 1470.8 321.096 1477.93 Q321.096 1485.04 322.901 1488.61 Q324.73 1492.15 328.341 1492.15 Q331.975 1492.15 333.781 1488.61 Q335.61 1485.04 335.61 1477.93 Q335.61 1470.8 333.781 1467.26 Q331.975 1463.7 328.341 1463.7 M328.341 1459.99 Q334.151 1459.99 337.207 1464.6 Q340.286 1469.18 340.286 1477.93 Q340.286 1486.66 337.207 1491.27 Q334.151 1495.85 328.341 1495.85 Q322.531 1495.85 319.452 1491.27 Q316.397 1486.66 316.397 1477.93 Q316.397 1469.18 319.452 1464.6 Q322.531 1459.99 328.341 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip440)" d="M859.287 1491.24 L875.606 1491.24 L875.606 1495.18 L853.662 1495.18 L853.662 1491.24 Q856.324 1488.49 860.908 1483.86 Q865.514 1479.21 866.695 1477.87 Q868.94 1475.34 869.819 1473.61 Q870.722 1471.85 870.722 1470.16 Q870.722 1467.4 868.778 1465.67 Q866.857 1463.93 863.755 1463.93 Q861.556 1463.93 859.102 1464.69 Q856.671 1465.46 853.894 1467.01 L853.894 1462.29 Q856.718 1461.15 859.171 1460.57 Q861.625 1459.99 863.662 1459.99 Q869.032 1459.99 872.227 1462.68 Q875.421 1465.37 875.421 1469.86 Q875.421 1471.99 874.611 1473.91 Q873.824 1475.8 871.718 1478.4 Q871.139 1479.07 868.037 1482.29 Q864.935 1485.48 859.287 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip440)" d="M895.421 1463.7 Q891.81 1463.7 889.981 1467.26 Q888.176 1470.8 888.176 1477.93 Q888.176 1485.04 889.981 1488.61 Q891.81 1492.15 895.421 1492.15 Q899.055 1492.15 900.861 1488.61 Q902.69 1485.04 902.69 1477.93 Q902.69 1470.8 900.861 1467.26 Q899.055 1463.7 895.421 1463.7 M895.421 1459.99 Q901.231 1459.99 904.287 1464.6 Q907.366 1469.18 907.366 1477.93 Q907.366 1486.66 904.287 1491.27 Q901.231 1495.85 895.421 1495.85 Q889.611 1495.85 886.532 1491.27 Q883.477 1486.66 883.477 1477.93 Q883.477 1469.18 886.532 1464.6 Q889.611 1459.99 895.421 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip440)" d="M925.583 1463.7 Q921.972 1463.7 920.143 1467.26 Q918.338 1470.8 918.338 1477.93 Q918.338 1485.04 920.143 1488.61 Q921.972 1492.15 925.583 1492.15 Q929.217 1492.15 931.023 1488.61 Q932.852 1485.04 932.852 1477.93 Q932.852 1470.8 931.023 1467.26 Q929.217 1463.7 925.583 1463.7 M925.583 1459.99 Q931.393 1459.99 934.449 1464.6 Q937.527 1469.18 937.527 1477.93 Q937.527 1486.66 934.449 1491.27 Q931.393 1495.85 925.583 1495.85 Q919.773 1495.85 916.694 1491.27 Q913.639 1486.66 913.639 1477.93 Q913.639 1469.18 916.694 1464.6 Q919.773 1459.99 925.583 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip440)" d="M1463.25 1463.7 Q1459.64 1463.7 1457.81 1467.26 Q1456.01 1470.8 1456.01 1477.93 Q1456.01 1485.04 1457.81 1488.61 Q1459.64 1492.15 1463.25 1492.15 Q1466.89 1492.15 1468.69 1488.61 Q1470.52 1485.04 1470.52 1477.93 Q1470.52 1470.8 1468.69 1467.26 Q1466.89 1463.7 1463.25 1463.7 M1463.25 1459.99 Q1469.06 1459.99 1472.12 1464.6 Q1475.2 1469.18 1475.2 1477.93 Q1475.2 1486.66 1472.12 1491.27 Q1469.06 1495.85 1463.25 1495.85 Q1457.44 1495.85 1454.36 1491.27 Q1451.31 1486.66 1451.31 1477.93 Q1451.31 1469.18 1454.36 1464.6 Q1457.44 1459.99 1463.25 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip440)" d="M1493.42 1463.7 Q1489.8 1463.7 1487.98 1467.26 Q1486.17 1470.8 1486.17 1477.93 Q1486.17 1485.04 1487.98 1488.61 Q1489.8 1492.15 1493.42 1492.15 Q1497.05 1492.15 1498.86 1488.61 Q1500.68 1485.04 1500.68 1477.93 Q1500.68 1470.8 1498.86 1467.26 Q1497.05 1463.7 1493.42 1463.7 M1493.42 1459.99 Q1499.23 1459.99 1502.28 1464.6 Q1505.36 1469.18 1505.36 1477.93 Q1505.36 1486.66 1502.28 1491.27 Q1499.23 1495.85 1493.42 1495.85 Q1487.61 1495.85 1484.53 1491.27 Q1481.47 1486.66 1481.47 1477.93 Q1481.47 1469.18 1484.53 1464.6 Q1487.61 1459.99 1493.42 

### 4.1.2 Cross-sectional aggregation forecasting

The `csa_forecast_()` function returns the forecasted values, while the
`csa_forecast_plot()` functions returns the plot. The arguments are
analogous to the fractional differencing plot function, noting that two
Beta parameters are needed.

In [1]:
p2 = csa_forecast_plot( NileData().NileMin , 30, pmle, qmle, sigcsa)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip500)" d="M328.341 1463.7 Q324.73 1463.7 322.901 1467.26 Q321.096 1470.8 321.096 1477.93 Q321.096 1485.04 322.901 1488.61 Q324.73 1492.15 328.341 1492.15 Q331.975 1492.15 333.781 1488.61 Q335.61 1485.04 335.61 1477.93 Q335.61 1470.8 333.781 1467.26 Q331.975 1463.7 328.341 1463.7 M328.341 1459.99 Q334.151 1459.99 337.207 1464.6 Q340.286 1469.18 340.286 1477.93 Q340.286 1486.66 337.207 1491.27 Q334.151 1495.85 328.341 1495.85 Q322.531 1495.85 319.452 1491.27 Q316.397 1486.66 316.397 1477.93 Q316.397 1469.18 319.452 1464.6 Q322.531 1459.99 328.341 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip500)" d="M859.287 1491.24 L875.606 1491.24 L875.606 1495.18 L853.662 1495.18 L853.662 1491.24 Q856.324 1488.49 860.908 1483.86 Q865.514 1479.21 866.695 1477.87 Q868.94 1475.34 869.819 1473.61 Q870.722 1471.85 870.722 1470.16 Q870.722 1467.4 868.778 1465.67 Q866.857 1463.93 863.755 1463.93 Q861.556 1463.93 859.102 1464.69 Q856.671 1465.46 853.894 1467.01 L853.894 1462.29 Q856.718 1461.15 859.171 1460.57 Q861.625 1459.99 863.662 1459.99 Q869.032 1459.99 872.227 1462.68 Q875.421 1465.37 875.421 1469.86 Q875.421 1471.99 874.611 1473.91 Q873.824 1475.8 871.718 1478.4 Q871.139 1479.07 868.037 1482.29 Q864.935 1485.48 859.287 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip500)" d="M895.421 1463.7 Q891.81 1463.7 889.981 1467.26 Q888.176 1470.8 888.176 1477.93 Q888.176 1485.04 889.981 1488.61 Q891.81 1492.15 895.421 1492.15 Q899.055 1492.15 900.861 1488.61 Q902.69 1485.04 902.69 1477.93 Q902.69 1470.8 900.861 1467.26 Q899.055 1463.7 895.421 1463.7 M895.421 1459.99 Q901.231 1459.99 904.287 1464.6 Q907.366 1469.18 907.366 1477.93 Q907.366 1486.66 904.287 1491.27 Q901.231 1495.85 895.421 1495.85 Q889.611 1495.85 886.532 1491.27 Q883.477 1486.66 883.477 1477.93 Q883.477 1469.18 886.532 1464.6 Q889.611 1459.99 895.421 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip500)" d="M925.583 1463.7 Q921.972 1463.7 920.143 1467.26 Q918.338 1470.8 918.338 1477.93 Q918.338 1485.04 920.143 1488.61 Q921.972 1492.15 925.583 1492.15 Q929.217 1492.15 931.023 1488.61 Q932.852 1485.04 932.852 1477.93 Q932.852 1470.8 931.023 1467.26 Q929.217 1463.7 925.583 1463.7 M925.583 1459.99 Q931.393 1459.99 934.449 1464.6 Q937.527 1469.18 937.527 1477.93 Q937.527 1486.66 934.449 1491.27 Q931.393 1495.85 925.583 1495.85 Q919.773 1495.85 916.694 1491.27 Q913.639 1486.66 913.639 1477.93 Q913.639 1469.18 916.694 1464.6 Q919.773 1459.99 925.583 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip500)" d="M1463.25 1463.7 Q1459.64 1463.7 1457.81 1467.26 Q1456.01 1470.8 1456.01 1477.93 Q1456.01 1485.04 1457.81 1488.61 Q1459.64 1492.15 1463.25 1492.15 Q1466.89 1492.15 1468.69 1488.61 Q1470.52 1485.04 1470.52 1477.93 Q1470.52 1470.8 1468.69 1467.26 Q1466.89 1463.7 1463.25 1463.7 M1463.25 1459.99 Q1469.06 1459.99 1472.12 1464.6 Q1475.2 1469.18 1475.2 1477.93 Q1475.2 1486.66 1472.12 1491.27 Q1469.06 1495.85 1463.25 1495.85 Q1457.44 1495.85 1454.36 1491.27 Q1451.31 1486.66 1451.31 1477.93 Q1451.31 1469.18 1454.36 1464.6 Q1457.44 1459.99 1463.25 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip500)" d="M1493.42 1463.7 Q1489.8 1463.7 1487.98 1467.26 Q1486.17 1470.8 1486.17 1477.93 Q1486.17 1485.04 1487.98 1488.61 Q1489.8 1492.15 1493.42 1492.15 Q1497.05 1492.15 1498.86 1488.61 Q1500.68 1485.04 1500.68 1477.93 Q1500.68 1470.8 1498.86 1467.26 Q1497.05 1463.7 1493.42 1463.7 M1493.42 1459.99 Q1499.23 1459.99 1502.28 1464.6 Q1505.36 1469.18 1505.36 1477.93 Q1505.36 1486.66 1502.28 1491.27 Q1499.23 1495.85 1493.42 1495.85 Q1487.61 1495.85 1484.53 1491.27 Q1481.47 1486.66 1481.47 1477.93 Q1481.47 1469.18 1484.53 1464.6 Q1487.61 1459.99 1493.4

### 4.1.3 Custom-HAR forecasting

The `har_forecast_()` function returns the forecasted values, while the
`har_forecast_plot()` functions returns the plot. Nonetheless, the
arguments are not analogous to the fractional differencing and
cross-sectional aggregation plot functions, given that the custom-HAR
model is estimated as part of the forecast.

Hence, the first argument is the time series to forecast and the second
argument is used to define the number of steps ahead to forecast as
before. The third optional argument, `flag`, is used to determine if the
the confidence bands should be included in the plot. The fourth optional
argument, `m`, is used to define the number of lags to use in the
custom-HAR model. The optional fifth argument is used to define the
standard deviation to plot the confidence bands.

In [1]:
p3 = har_forecast_plot( NileData().NileMin , 30; flag=true, m=[1, 7])

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip560)" d="M328.341 1463.7 Q324.73 1463.7 322.901 1467.26 Q321.096 1470.8 321.096 1477.93 Q321.096 1485.04 322.901 1488.61 Q324.73 1492.15 328.341 1492.15 Q331.975 1492.15 333.781 1488.61 Q335.61 1485.04 335.61 1477.93 Q335.61 1470.8 333.781 1467.26 Q331.975 1463.7 328.341 1463.7 M328.341 1459.99 Q334.151 1459.99 337.207 1464.6 Q340.286 1469.18 340.286 1477.93 Q340.286 1486.66 337.207 1491.27 Q334.151 1495.85 328.341 1495.85 Q322.531 1495.85 319.452 1491.27 Q316.397 1486.66 316.397 1477.93 Q316.397 1469.18 319.452 1464.6 Q322.531 1459.99 328.341 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip560)" d="M859.287 1491.24 L875.606 1491.24 L875.606 1495.18 L853.662 1495.18 L853.662 1491.24 Q856.324 1488.49 860.908 1483.86 Q865.514 1479.21 866.695 1477.87 Q868.94 1475.34 869.819 1473.61 Q870.722 1471.85 870.722 1470.16 Q870.722 1467.4 868.778 1465.67 Q866.857 1463.93 863.755 1463.93 Q861.556 1463.93 859.102 1464.69 Q856.671 1465.46 853.894 1467.01 L853.894 1462.29 Q856.718 1461.15 859.171 1460.57 Q861.625 1459.99 863.662 1459.99 Q869.032 1459.99 872.227 1462.68 Q875.421 1465.37 875.421 1469.86 Q875.421 1471.99 874.611 1473.91 Q873.824 1475.8 871.718 1478.4 Q871.139 1479.07 868.037 1482.29 Q864.935 1485.48 859.287 1491.24 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip560)" d="M895.421 1463.7 Q891.81 1463.7 889.981 1467.26 Q888.176 1470.8 888.176 1477.93 Q888.176 1485.04 889.981 1488.61 Q891.81 1492.15 895.421 1492.15 Q899.055 1492.15 900.861 1488.61 Q902.69 1485.04 902.69 1477.93 Q902.69 1470.8 900.861 1467.26 Q899.055 1463.7 895.421 1463.7 M895.421 1459.99 Q901.231 1459.99 904.287 1464.6 Q907.366 1469.18 907.366 1477.93 Q907.366 1486.66 904.287 1491.27 Q901.231 1495.85 895.421 1495.85 Q889.611 1495.85 886.532 1491.27 Q883.477 1486.66 883.477 1477.93 Q883.477 1469.18 886.532 1464.6 Q889.611 1459.99 895.421 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip560)" d="M925.583 1463.7 Q921.972 1463.7 920.143 1467.26 Q918.338 1470.8 918.338 1477.93 Q918.338 1485.04 920.143 1488.61 Q921.972 1492.15 925.583 1492.15 Q929.217 1492.15 931.023 1488.61 Q932.852 1485.04 932.852 1477.93 Q932.852 1470.8 931.023 1467.26 Q929.217 1463.7 925.583 1463.7 M925.583 1459.99 Q931.393 1459.99 934.449 1464.6 Q937.527 1469.18 937.527 1477.93 Q937.527 1486.66 934.449 1491.27 Q931.393 1495.85 925.583 1495.85 Q919.773 1495.85 916.694 1491.27 Q913.639 1486.66 913.639 1477.93 Q913.639 1469.18 916.694 1464.6 Q919.773 1459.99 925.583 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip560)" d="M1463.25 1463.7 Q1459.64 1463.7 1457.81 1467.26 Q1456.01 1470.8 1456.01 1477.93 Q1456.01 1485.04 1457.81 1488.61 Q1459.64 1492.15 1463.25 1492.15 Q1466.89 1492.15 1468.69 1488.61 Q1470.52 1485.04 1470.52 1477.93 Q1470.52 1470.8 1468.69 1467.26 Q1466.89 1463.7 1463.25 1463.7 M1463.25 1459.99 Q1469.06 1459.99 1472.12 1464.6 Q1475.2 1469.18 1475.2 1477.93 Q1475.2 1486.66 1472.12 1491.27 Q1469.06 1495.85 1463.25 1495.85 Q1457.44 1495.85 1454.36 1491.27 Q1451.31 1486.66 1451.31 1477.93 Q1451.31 1469.18 1454.36 1464.6 Q1457.44 1459.99 1463.25 1459.99 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip560)" d="M1493.42 1463.7 Q1489.8 1463.7 1487.98 1467.26 Q1486.17 1470.8 1486.17 1477.93 Q1486.17 1485.04 1487.98 1488.61 Q1489.8 1492.15 1493.42 1492.15 Q1497.05 1492.15 1498.86 1488.61 Q1500.68 1485.04 1500.68 1477.93 Q1500.68 1470.8 1498.86 1467.26 Q1497.05 1463.7 1493.42 1463.7 M1493.42 1459.99 Q1499.23 1459.99 1502.28 1464.6 Q1505.36 1469.18 1505.36 1477.93 Q1505.36 1486.66 1502.28 1491.27 Q1499.23 1495.85 1493.42 1495.85 Q1487.61 1495.85 1484.53 1491.27 Q1481.47 1486.66 1481.47 1477.93 Q1481.47 1469.18 1484.53 1464.6 Q1487.61 1459.99 1493.42 

### 4.1.4 Comparing the forecasts

We generate a plot with the three forecasts using the `@layout` macro
from the `Plots.jl` package.

In [1]:
l = @layout [a b c]
theme(:ggplot2)
plot(p1, p2, p3, layout = l, size = (800, 300), xlabel = "", ylabel = "" )
xlims!(500, 673)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
<path clip-path="url(#clip620)" d="M199.356 1152.61 L217.712 1152.61 L217.712 1156.54 L203.638 1156.54 L203.638 1165.02 Q204.657 1164.67 205.675 1164.51 Q206.694 1164.32 207.712 1164.32 Q213.499 1164.32 216.879 1167.49 Q220.259 1170.66 220.259 1176.08 Q220.259 1181.66 216.787 1184.76 Q213.314 1187.84 206.995 1187.84 Q204.819 1187.84 202.55 1187.47 Q200.305 1187.1 197.898 1186.36 L197.898 1181.66 Q199.981 1182.79 202.203 1183.35 Q204.425 1183.9 206.902 1183.9 Q210.907 1183.9 213.245 1181.8 Q215.583 1179.69 215.583 1176.08 Q215.583 1172.47 213.245 1170.36 Q210.907 1168.26 206.902 1168.26 Q205.027 1168.26 203.152 1168.67 Q201.3 1169.09 199.356 1169.97 L199.356 1152.61 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M239.472 1155.69 Q235.86 1155.69 234.032 1159.25 Q232.226 1162.79 232.226 1169.92 Q232.226 1177.03 234.032 1180.59 Q235.86 1184.14 239.472 1184.14 Q243.106 1184.14 244.911 1180.59 Q246.74 1177.03 246.74 1169.92 Q246.74 1162.79 244.911 1159.25 Q243.106 1155.69 239.472 1155.69 M239.472 1151.98 Q245.282 1151.98 248.337 1156.59 Q251.416 1161.17 251.416 1169.92 Q251.416 1178.65 248.337 1183.26 Q245.282 1187.84 239.472 1187.84 Q233.661 1187.84 230.583 1183.26 Q227.527 1178.65 227.527 1169.92 Q227.527 1161.17 230.583 1156.59 Q233.661 1151.98 239.472 1151.98 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M269.633 1155.69 Q266.022 1155.69 264.194 1159.25 Q262.388 1162.79 262.388 1169.92 Q262.388 1177.03 264.194 1180.59 Q266.022 1184.14 269.633 1184.14 Q273.268 1184.14 275.073 1180.59 Q276.902 1177.03 276.902 1169.92 Q276.902 1162.79 275.073 1159.25 Q273.268 1155.69 269.633 1155.69 M269.633 1151.98 Q275.444 1151.98 278.499 1156.59 Q281.578 1161.17 281.578 1169.92 Q281.578 1178.65 278.499 1183.26 Q275.444 1187.84 269.633 1187.84 Q263.823 1187.84 260.745 1183.26 Q257.689 1178.65 257.689 1169.92 Q257.689 1161.17 260.745 1156.59 Q263.823 1151.98 269.633 1151.98 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M418.135 1152.61 L436.491 1152.61 L436.491 1156.54 L422.417 1156.54 L422.417 1165.02 Q423.436 1164.67 424.455 1164.51 Q425.473 1164.32 426.492 1164.32 Q432.279 1164.32 435.658 1167.49 Q439.038 1170.66 439.038 1176.08 Q439.038 1181.66 435.566 1184.76 Q432.093 1187.84 425.774 1187.84 Q423.598 1187.84 421.33 1187.47 Q419.084 1187.1 416.677 1186.36 L416.677 1181.66 Q418.76 1182.79 420.982 1183.35 Q423.205 1183.9 425.681 1183.9 Q429.686 1183.9 432.024 1181.8 Q434.362 1179.69 434.362 1176.08 Q434.362 1172.47 432.024 1170.36 Q429.686 1168.26 425.681 1168.26 Q423.806 1168.26 421.931 1168.67 Q420.08 1169.09 418.135 1169.97 L418.135 1152.61 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M448.297 1152.61 L466.653 1152.61 L466.653 1156.54 L452.579 1156.54 L452.579 1165.02 Q453.598 1164.67 454.616 1164.51 Q455.635 1164.32 456.653 1164.32 Q462.44 1164.32 465.82 1167.49 Q469.2 1170.66 469.2 1176.08 Q469.2 1181.66 465.727 1184.76 Q462.255 1187.84 455.936 1187.84 Q453.76 1187.84 451.491 1187.47 Q449.246 1187.1 446.839 1186.36 L446.839 1181.66 Q448.922 1182.79 451.144 1183.35 Q453.366 1183.9 455.843 1183.9 Q459.848 1183.9 462.186 1181.8 Q464.524 1179.69 464.524 1176.08 Q464.524 1172.47 462.186 1170.36 Q459.848 1168.26 455.843 1168.26 Q453.968 1168.26 452.093 1168.67 Q450.241 1169.09 448.297 1169.97 L448.297 1152.61 Z" fill="#4c4c4c" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip620)" d="M488.413 1155.69 Q484.801 1155.69 482.973 1159.25 Q481.167 1162.79 481.167 1169.92 Q481.167 1177.03 482.973 1180.59 Q484.801 1184.14 488.413 1184.14 Q492.047 1184.14 493.852 1180.59 Q495.681 1177.03 495.681 1169.92 Q495.681 1162.79 493.852 1159.25 Q492.047 1155.69 488.413 1155.69 M488.413 1151.98 Q494.223 1151.98 497.278 1156.59 Q500.357 1161

**End of the notebook.**